# Core - Series 2

In [1]:
from ripe_wrapper.database.database_table import DatabaseTable
from ripe_wrapper.database.request_table import RequestTable
from ripe_wrapper.database.request_pseudosection_table import RequestPseudosectionTable
DatabaseTable.DATABASE_PATH = "request_data.db"
import pandas as pd 
import csv 
import sqlite3
from IPython.display import display
from analysis_util.df_manipulation import create_resolver_column, create_continent_name_column
import base64
from ripe.atlas.sagan.helpers import abuf

In [2]:
conn = sqlite3.connect("data/request_data.db")

In [3]:
server_results = pd.read_sql("SELECT * from requests", conn)

In [4]:
server_results

id                                question_name   timestamp  \
0                1   53804.1647648002.0.membrain-it.technology.  1647648002   
1                2   53804.1647648002.0.membrain-it.technology.  1647648002   
2                3   24355.1647648001.0.membrain-it.technology.  1647648002   
3                4   15407.1647648002.0.membrain-it.technology.  1647648002   
4                5   15407.1647648002.0.membrain-it.technology.  1647648002   
...            ...                                          ...         ...   
13026500  13026501  51108.1648224049.10.membrain-it.technology.  1648224050   
13026501  13026502  21516.1648224052.10.membrain-it.technology.  1648224050   
13026502  13026503  31398.1648224050.10.membrain-it.technology.  1648224050   
13026503  13026504  52849.1648224050.18.membrain-it.technology.  1648224050   
13026504  13026505  50552.1648224050.10.membrain-it.technology.  1648224050   

          response_size              backend_resolver proto raw_data flags  \
0                     2                162.158.148.71   UDP     None         
1                     2                162.158.148.71   TCP     None         
2                     2                172.68.220.148   UDP     None         
3                     2                162.158.148.71   UDP     None         
4                     2                162.158.148.71   TCP     None         
...                 ...                           ...   ...      ...   ...   
13026500              4  2400:cb00:11:1024::6ca2:da12   UDP     None         
13026501              4                  85.38.28.180   UDP     None         
13026502              4                   172.253.8.4   UDP     None    cd   
13026503              4   2001:878:0:e000:82:e2:a1:22   TCP     None         
13026504              4                 162.158.37.75   UDP     None         

                                             header  query_count  ans_count  \
0         opcode: QUERY, status: NOERROR, id: 15522            1          0   
1         opcode: QUERY, status: NOERROR, id: 15522            1          0   
2         opcode: QUERY, status: NOERROR, id: 23449            1          0   
3         opcode: QUERY, status: NOERROR, id: 64650            1          0   
4         opcode: QUERY, status: NOERROR, id: 64650            1          0   
...                                             ...          ...        ...   
13026500  opcode: QUERY, status: NOERROR, id: 39461            1          0   
13026501  opcode: QUERY, status: NOERROR, id: 56597            1          0   
13026502  opcode: QUERY, status: NOERROR, id: 44793            1          0   
13026503  opcode: QUERY, status: NOERROR, id: 63872            1          0   
13026504  opcode: QUERY, status: NOERROR, id: 22445            1          0   

          auth_count  addit_count  \
0                  0            1   
1                  0            1   
2                  0            1   
3                  0            1   
4                  0            1   
...              ...          ...   
13026500           0            1   
13026501           0            1   
13026502           0            1   
13026503           0            1   
13026504           0            1   

                                                   question  udp_size  
0         53804.1647648002.0.membrain-it.technology. IN ...    1452.0  
1         53804.1647648002.0.membrain-it.technology. IN ...    1452.0  
2         24355.1647648001.0.membrain-it.technology. IN ...    1452.0  
3         15407.1647648002.0.membrain-it.technology. IN ...    1452.0  
4         15407.1647648002.0.membrain-it.technology. IN ...    1452.0  
...                                                     ...       ...  
13026500  51108.1648224049.10.membrain-it.technology. IN...    1452.0  
13026501  21516.1648224052.10.membrain-it.technology. IN...     512.0  
13026502  31398.1648224050.10.membrain-it.technology. IN...    1400.0  
13026503  52849.

In [5]:
conn = sqlite3.connect("data/ripe_results_fallback.db")
ripe_results = pd.read_sql(f"""SELECT r.msm_id, r.prb_id, r.sub_id, r.rt, r.proto as frontend_proto, r.dst_addr, r.question_name, r.abuf, r.qbuf,
                                 m.use_probe_resolver, m.af, m.start_time, m.stop_time,
                                 mp.timestamp, mp.stored_timestamp,
                                 a.number as asn, 
                                 p.continent_code,
                                 e.error, e.description
                           FROM measurements m 
                           JOIN measurement_probes mp on m.id == mp.msm_id 
                           JOIN results r ON r.msm_id = m.id and mp.prb_id = r.prb_id
                           JOIN probes p on p.id = r.prb_id 
                           JOIN autonomous_systems a ON p.asn_v4 = a.number
                           LEFT JOIN errors e ON r.msm_id = e.msm_id AND r.prb_id = e.prb_id AND r.sub_id = e.sub_id""", conn)

In [7]:
def get_question_name(row):
    if row["question_name"] != "None": 
        return row["question_name"]
    data_qbuf = row["qbuf"]
    try:
        test = abuf.AbufParser.parse(base64.b64decode(data_qbuf))
        if test is not None and "QuestionSection" in test and len(test["QuestionSection"]) > 0: 
            question = test["QuestionSection"][0]
            if "Qname" in question:
                return question["Qname"]
            else:
                return None
        else: 
            return None
    except: 
        return None

In [8]:
def create_failure_column(row):
    if row["rt"] == "None":
        return "failure"
    return "ok"

In [9]:
ripe_results["resolver"] = ripe_results.apply(create_resolver_column, axis = 1)
ripe_results["continent"] = ripe_results.apply(create_continent_name_column, axis = 1)

In [10]:
ripe_results["question_name"] = ripe_results.apply(get_question_name, axis = 1)
ripe_results["status"] = ripe_results.apply(create_failure_column, axis = 1)

# All results have unique domains! 

In [11]:
test = ripe_results.groupby(["question_name", "af"], as_index=False).size().sort_values("size", ascending = False)
display(test)
display(test.groupby("af", as_index=False).size())

question_name  af  size
0         10001.1647648006.0.membrain-it.technology.   4     1
3051171  34992.1648191672.12.membrain-it.technology.   6     1
3051177   34992.1648195227.3.membrain-it.technology.   4     1
3051176   34992.1648195219.6.membrain-it.technology.   4     1
3051175   34992.1648195218.2.membrain-it.technology.   4     1
...                                              ...  ..   ...
1525590   22150.1647961268.8.membrain-it.technology.   4     1
1525591   22150.1647961268.9.membrain-it.technology.   4     1
1525592   22150.1647964810.0.membrain-it.technology.   4     1
1525593   22150.1647964811.1.membrain-it.technology.   4     1
4576756   55859.1648234840.7.membrain-it.technology.   4     1

[4576757 rows x 3 columns]

af     size
0   4  3241545
1   6  1335212

In [12]:
df_merged = ripe_results.merge(server_results, on="question_name", how="left", suffixes = ('_ripe','_server'))    

In [13]:
df_merged

msm_id  prb_id  sub_id        rt frontend_proto     dst_addr  \
0         39507178   14604       1  1021.576            UDP      1.1.1.1   
1         39507178   14604       1  1021.576            UDP      1.1.1.1   
2         39507178   29376       1    44.184            UDP      1.1.1.1   
3         39507178   29376       1    44.184            UDP      1.1.1.1   
4         39507178   10001       1   746.388            UDP      1.1.1.1   
...            ...     ...     ...       ...            ...          ...   
12328024  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328025  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328026  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328027  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328028  39712680   55660       2  1606.725            UDP  192.168.4.1   

                                        question_name  \
0          14604.1647647999.0.membrain-it.technology.   
1          14604.1647647999.0.membrain-it.technology.   
2          29376.1647647999.0.membrain-it.technology.   
3          29376.1647647999.0.membrain-it.technology.   
4          10001.1647648006.0.membrain-it.technology.   
...                                               ...   
12328024  55660.1648235147.21.membrain-it.technology.   
12328025  55660.1648235147.21.membrain-it.technology.   
12328026  55660.1648235147.21.membrain-it.technology.   
12328027  55660.1648235147.21.membrain-it.technology.   
12328028  55660.1648235147.21.membrain-it.technology.   

                                                       abuf  \
0         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp2DgAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

                                                       qbuf  \
0         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp0BAAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

         use_probe_resolver  ...  proto  raw_data  flags  \
0                      None  ...    UDP      None          
1                      None  ...    TCP      None          
2                      None  ...    UDP      None          
3                      None  ...    TCP      None          
4                      None  ...    UDP      None          
...                     ...  ...    ...       ...    ...   
12328024               True  ...    TCP      None          
12328025               True  ...    UDP      None     cd   
12328026               True  ...    TCP      None     cd   
12328027               True  ...    UDP      None          
12328028               True  ...    TCP      None     cd   

                                             header  query_count  ans_count  \
0         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
1         opcode: QUE

In [14]:
df_merged = df_merged[(df_merged["timestamp_server"].isna()) | (df_merged["timestamp_server"] >= df_merged["start_time"])]
df_merged = df_merged[df_merged["timestamp_server"].isna() | (df_merged["timestamp_server"] <= df_merged["stop_time"])]


In [15]:
df_merged

msm_id  prb_id  sub_id        rt frontend_proto     dst_addr  \
0         39507178   14604       1  1021.576            UDP      1.1.1.1   
1         39507178   14604       1  1021.576            UDP      1.1.1.1   
2         39507178   29376       1    44.184            UDP      1.1.1.1   
3         39507178   29376       1    44.184            UDP      1.1.1.1   
4         39507178   10001       1   746.388            UDP      1.1.1.1   
...            ...     ...     ...       ...            ...          ...   
12328024  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328025  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328026  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328027  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328028  39712680   55660       2  1606.725            UDP  192.168.4.1   

                                        question_name  \
0          14604.1647647999.0.membrain-it.technology.   
1          14604.1647647999.0.membrain-it.technology.   
2          29376.1647647999.0.membrain-it.technology.   
3          29376.1647647999.0.membrain-it.technology.   
4          10001.1647648006.0.membrain-it.technology.   
...                                               ...   
12328024  55660.1648235147.21.membrain-it.technology.   
12328025  55660.1648235147.21.membrain-it.technology.   
12328026  55660.1648235147.21.membrain-it.technology.   
12328027  55660.1648235147.21.membrain-it.technology.   
12328028  55660.1648235147.21.membrain-it.technology.   

                                                       abuf  \
0         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp2DgAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

                                                       qbuf  \
0         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp0BAAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

         use_probe_resolver  ...  proto  raw_data  flags  \
0                      None  ...    UDP      None          
1                      None  ...    TCP      None          
2                      None  ...    UDP      None          
3                      None  ...    TCP      None          
4                      None  ...    UDP      None          
...                     ...  ...    ...       ...    ...   
12328024               True  ...    TCP      None          
12328025               True  ...    UDP      None     cd   
12328026               True  ...    TCP      None     cd   
12328027               True  ...    UDP      None          
12328028               True  ...    TCP      None     cd   

                                             header  query_count  ans_count  \
0         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
1         opcode: QUE

In [16]:
import math
def create_detailed_failure_column(row):
    if row["rt"] == "None":
        if math.isnan(row["timestamp_server"]):
            return "never requested failure"
        else:
            return "failure"
    if math.isnan(row["timestamp_server"]):
        return "never requested ok"
    return "ok"

In [17]:
df_merged["status_detail"] = df_merged.apply(create_detailed_failure_column, axis=1)

In [18]:
test = df_merged.groupby("question_name", as_index = False).head(1)

# Failure rates

In [19]:
data_v4 = test[test['af'] == 4]
data_v6 = test[test['af'] == 6]
print("IPv4")
df_grouped = data_v4.groupby(["question_name"]).tail(1)
display(pd.crosstab(df_grouped["status_detail"], df_grouped["resolver"]))
display(pd.crosstab(df_grouped["status_detail"], df_grouped["resolver"], normalize="columns"))
display(pd.crosstab(df_grouped["status"], df_grouped["resolver"], normalize="columns"))
print("IPv6")
df_grouped = data_v6.groupby(["question_name"]).tail(1)
display(pd.crosstab(df_grouped["status_detail"], df_grouped["resolver"]))
display(pd.crosstab(df_grouped["status_detail"], df_grouped["resolver"], normalize="columns"))
display(pd.crosstab(df_grouped["status"], df_grouped["resolver"], normalize="columns"))

IPv4


resolver                 CleanBrowsing  Cloudflare  Comodo  Google  Neustar  \
status_detail                                                                 
failure                           3156        1638   71470    8612    18231   
never requested failure           6273        6361   15067    5734     7938   
never requested ok                1247        2544    3754    2678      910   
ok                              284089      284311  204423  277776   267647   

resolver                 OpenDNS  OpenNIC  Probe Resolver   Quad9  \
status_detail                                                       
failure                    11447     1397           14315   22184   
never requested failure     5395   286589            4323   26268   
never requested ok          1842      458            3857    2023   
ok                        276047     6068          271266  244244   

resolver                 UncensoredDNS  Yandex  
status_detail                                   
failure                           1767   13172  
never requested failure         252845   11139  
never requested ok                 554     466  
ok                               39361  269682

resolver                 CleanBrowsing  Cloudflare    Comodo    Google  \
status_detail                                                            
failure                       0.010707    0.005555  0.242506  0.029213   
never requested failure       0.021281    0.021573  0.051124  0.019450   
never requested ok            0.004230    0.008628  0.012738  0.009084   
ok                            0.963781    0.964243  0.693632  0.942252   

resolver                  Neustar   OpenDNS   OpenNIC  Probe Resolver  \
status_detail                                                           
failure                  0.061857  0.038839  0.004743        0.048730   
never requested failure  0.026933  0.018305  0.973098        0.014716   
never requested ok       0.003088  0.006250  0.001555        0.013130   
ok                       0.908121  0.936607  0.020604        0.923424   

resolver                    Quad9  UncensoredDNS    Yandex  
status_detail                                               
failure                  0.075272       0.005999  0.044733  
never requested failure  0.089129       0.858478  0.037829  
never requested ok       0.006864       0.001881  0.001583  
ok                       0.828735       0.133641  0.915856

resolver  CleanBrowsing  Cloudflare   Comodo    Google   Neustar   OpenDNS  \
status                                                                       
failure        0.031988    0.027129  0.29363  0.048664  0.088791  0.057144   
ok             0.968012    0.972871  0.70637  0.951336  0.911209  0.942856   

resolver   OpenNIC  Probe Resolver     Quad9  UncensoredDNS    Yandex  
status                                                                 
failure   0.977841        0.063446  0.164401       0.864478  0.082562  
ok        0.022159        0.936554  0.835599       0.135522  0.917438

IPv6


resolver                 CleanBrowsing  Cloudflare  Google  Neustar  OpenDNS  \
status_detail                                                                  
failure                           2088        1891   39779    44104    48974   
never requested failure           8728        8236    9017     9130     8879   
never requested ok                 747        1079    1112      240      611   
ok                              122151      121615   83827    80136    75291   

resolver                 OpenNIC  Probe Resolver  Quad9  UncensoredDNS  Yandex  
status_detail                                                                   
failure                       75            5057  27686           1575    6870  
never requested failure   132147            1652   8939          13454    9021  
never requested ok            12            1093    919           1433     143  
ok                           828          124707  96110         117177  117613

resolver                 CleanBrowsing  Cloudflare    Google   Neustar  \
status_detail                                                            
failure                       0.015615    0.014237  0.297446  0.330095   
never requested failure       0.065274    0.062008  0.067424  0.068333   
never requested ok            0.005587    0.008124  0.008315  0.001796   
ok                            0.913524    0.915631  0.626814  0.599775   

resolver                  OpenDNS   OpenNIC  Probe Resolver     Quad9  \
status_detail                                                           
failure                  0.366147  0.000564        0.038163  0.207147   
never requested failure  0.066383  0.993124        0.012467  0.066882   
never requested ok       0.004568  0.000090        0.008248  0.006876   
ok                       0.562902  0.006223        0.941121  0.719096   

resolver                 UncensoredDNS    Yandex  
status_detail                                     
failure                       0.011785  0.051404  
never requested failure       0.100674  0.067499  
never requested ok            0.010723  0.001070  
ok                            0.876817  0.880027

resolver  CleanBrowsing  Cloudflare    Google   Neustar  OpenDNS   OpenNIC  \
status                                                                       
failure        0.080889    0.076245  0.364871  0.398428  0.43253  0.993687   
ok             0.919111    0.923755  0.635129  0.601572  0.56747  0.006313   

resolver  Probe Resolver     Quad9  UncensoredDNS    Yandex  
status                                                       
failure         0.050631  0.274028        0.11246  0.118903  
ok              0.949369  0.725972        0.88754  0.881097

In [20]:
pd.crosstab(ripe_results["resolver"], ripe_results["error"])
pd.crosstab(ripe_results["resolver"], ripe_results["error"], normalize="index")

error             socket   timeout
resolver                          
CleanBrowsing   0.002316  0.997684
Cloudflare      0.002367  0.997633
Comodo          0.000012  0.999988
Google          0.000712  0.999288
Neustar         0.000566  0.999434
OpenDNS         0.000589  0.999411
OpenNIC         0.000119  0.999881
Probe Resolver  0.031916  0.968084
Quad9           0.000528  0.999472
UncensoredDNS   0.000167  0.999833
Yandex          0.001192  0.998808

# Prepare Request data

In [21]:
df_merged["response_size"].unique()

array([ 4.,  2., nan])

In [22]:
data_2kb = df_merged[df_merged["response_size"] == 2]
data_4kb = df_merged[df_merged["response_size"] == 4]

q1 = data_2kb["question_name"].unique()
q2 = data_4kb["question_name"].unique()

def intersection(lst1, lst2):
    return list(set(lst1) & set(lst2))

both_response_sizes = intersection(q1, q2)



In [141]:
pd.crosstab(df_merged["response_size"], df_merged["resolver"], normalize = "columns")

resolver       CleanBrowsing  Cloudflare    Comodo    Google   Neustar  \
response_size                                                            
2.0                 0.804712    0.567089  0.690705  0.624352  0.630454   
4.0                 0.195288    0.432911  0.309295  0.375648  0.369546   

resolver        OpenDNS   OpenNIC  Probe Resolver     Quad9  UncensoredDNS  \
response_size                                                                
2.0            0.697104  0.567321        0.570146  0.649671        0.63956   
4.0            0.302896  0.432679        0.429854  0.350329        0.36044   

resolver         Yandex  
response_size            
2.0            0.603996  
4.0            0.396004

In [23]:
data_2kb = df_merged[df_merged["response_size"] == 2]
data_2kb = data_2kb[~data_2kb["question_name"].isin(both_response_sizes)]

In [24]:
data_4kb = df_merged[df_merged["response_size"] == 4]
data_4kb = data_4kb[~data_4kb["question_name"].isin(both_response_sizes)]

In [25]:
data_both_response_sizes = df_merged[df_merged["question_name"].isin(both_response_sizes)]

In [26]:
data_2kb

msm_id  prb_id  sub_id        rt frontend_proto     dst_addr  \
2         39507178   29376       1    44.184            UDP      1.1.1.1   
3         39507178   29376       1    44.184            UDP      1.1.1.1   
22        39507178   10120       1    76.246            UDP      1.1.1.1   
23        39507178   10120       1    76.246            UDP      1.1.1.1   
24        39507178   10141       1    59.109            UDP      1.1.1.1   
...            ...     ...     ...       ...            ...          ...   
12328024  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328025  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328026  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328027  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328028  39712680   55660       2  1606.725            UDP  192.168.4.1   

                                        question_name  \
2          29376.1647647999.0.membrain-it.technology.   
3          29376.1647647999.0.membrain-it.technology.   
22         10120.1647648004.0.membrain-it.technology.   
23         10120.1647648004.0.membrain-it.technology.   
24         10141.1647648004.0.membrain-it.technology.   
...                                               ...   
12328024  55660.1648235147.21.membrain-it.technology.   
12328025  55660.1648235147.21.membrain-it.technology.   
12328026  55660.1648235147.21.membrain-it.technology.   
12328027  55660.1648235147.21.membrain-it.technology.   
12328028  55660.1648235147.21.membrain-it.technology.   

                                                       abuf  \
2         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
22        WEiDgAABAAAAAAABBTEwMTIwCjE2NDc2NDgwMDQBMAttZW...   
23        WEiDgAABAAAAAAABBTEwMTIwCjE2NDc2NDgwMDQBMAttZW...   
24        L5uDgAABAAAAAAABBTEwMTQxCjE2NDc2NDgwMDQBMAttZW...   
...                                                     ...   
12328024  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

                                                       qbuf  \
2         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
22        WEgBAAABAAAAAAABBTEwMTIwCjE2NDc2NDgwMDQBMAttZW...   
23        WEgBAAABAAAAAAABBTEwMTIwCjE2NDc2NDgwMDQBMAttZW...   
24        L5sBAAABAAAAAAABBTEwMTQxCjE2NDc2NDgwMDQBMAttZW...   
...                                                     ...   
12328024  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

         use_probe_resolver  ...  raw_data  flags  \
2                      None  ...      None          
3                      None  ...      None          
22                     None  ...      None          
23                     None  ...      None          
24                     None  ...      None          
...                     ...  ...       ...    ...   
12328024               True  ...      None          
12328025               True  ...      None     cd   
12328026               True  ...      None     cd   
12328027               True  ...      None          
12328028               True  ...      None     cd   

                                             header  query_count  ans_count  \
2          opcode: QUERY, status: NOERROR, id: 8127          1.0        0.0   
3          opcode: QUERY, status: NOERROR, id: 8127          1.0        0.0   
22        opcode: QUERY, s

In [27]:
data_4kb

msm_id  prb_id  sub_id        rt frontend_proto      dst_addr  \
0         39507178   14604       1  1021.576            UDP       1.1.1.1   
1         39507178   14604       1  1021.576            UDP       1.1.1.1   
4         39507178   10001       1   746.388            UDP       1.1.1.1   
5         39507178   10001       1   746.388            UDP       1.1.1.1   
6         39507178   10001       1   746.388            UDP       1.1.1.1   
...            ...     ...     ...       ...            ...           ...   
12129374  39706802   55603       2   109.768            UDP  192.168.1.77   
12129375  39706802   55603       2   109.768            UDP  192.168.1.77   
12129384  39706802   55685       2  1055.764            UDP       1.1.1.1   
12129385  39706802   55685       2  1055.764            UDP       1.1.1.1   
12129386  39706802   55685       2  1055.764            UDP       1.1.1.1   

                                        question_name  \
0          14604.1647647999.0.membrain-it.technology.   
1          14604.1647647999.0.membrain-it.technology.   
4          10001.1647648006.0.membrain-it.technology.   
5          10001.1647648006.0.membrain-it.technology.   
6          10001.1647648006.0.membrain-it.technology.   
...                                               ...   
12129374  55603.1648224038.21.membrain-it.technology.   
12129375  55603.1648224038.21.membrain-it.technology.   
12129384  55685.1648224036.21.membrain-it.technology.   
12129385  55685.1648224036.21.membrain-it.technology.   
12129386  55685.1648224036.21.membrain-it.technology.   

                                                       abuf  \
0         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
4         yp2DgAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
5         yp2DgAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
6         yp2DgAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12129374  EwiDgAABAAAAAAABBTU1NjAzCjE2NDgyMjQwMzgCMjELbW...   
12129375  EwiDgAABAAAAAAABBTU1NjAzCjE2NDgyMjQwMzgCMjELbW...   
12129384  ZD+DgAABAAAAAAABBTU1Njg1CjE2NDgyMjQwMzYCMjELbW...   
12129385  ZD+DgAABAAAAAAABBTU1Njg1CjE2NDgyMjQwMzYCMjELbW...   
12129386  ZD+DgAABAAAAAAABBTU1Njg1CjE2NDgyMjQwMzYCMjELbW...   

                                                       qbuf  \
0         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
4         yp0BAAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
5         yp0BAAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
6         yp0BAAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12129374  EwgBAAABAAAAAAABBTU1NjAzCjE2NDgyMjQwMzgCMjELbW...   
12129375  EwgBAAABAAAAAAABBTU1NjAzCjE2NDgyMjQwMzgCMjELbW...   
12129384  ZD8BAAABAAAAAAABBTU1Njg1CjE2NDgyMjQwMzYCMjELbW...   
12129385  ZD8BAAABAAAAAAABBTU1Njg1CjE2NDgyMjQwMzYCMjELbW...   
12129386  ZD8BAAABAAAAAAABBTU1Njg1CjE2NDgyMjQwMzYCMjELbW...   

         use_probe_resolver  ...  raw_data  flags  \
0                      None  ...      None          
1                      None  ...      None          
4                      None  ...      None          
5                      None  ...      None          
6                      None  ...      None          
...                     ...  ...       ...    ...   
12129374               True  ...      None     cd   
12129375               True  ...      None     cd   
12129384               True  ...      None          
12129385               True  ...      None          
12129386               True  ...      None          

                                             header  query_count  ans_count  \
0         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
1         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
4          opc

In [28]:
data_both_response_sizes

msm_id  prb_id  sub_id        rt frontend_proto       dst_addr  \
58        39507178   10317       1  1547.633            UDP        1.1.1.1   
59        39507178   10317       1  1547.633            UDP        1.1.1.1   
60        39507178   10317       1  1547.633            UDP        1.1.1.1   
61        39507178   10317       1  1547.633            UDP        1.1.1.1   
62        39507178   10317       1  1547.633            UDP        1.1.1.1   
...            ...     ...     ...       ...            ...            ...   
12129383  39706802   55662       2  1102.691            UDP      10.0.3.34   
12129395  39706802   55833       2   597.475            UDP  192.168.1.254   
12129396  39706802   55833       2   597.475            UDP  192.168.1.254   
12129397  39706802   55833       2   597.475            UDP  192.168.1.254   
12129398  39706802   55833       2   597.475            UDP  192.168.1.254   

                                        question_name  \
58         10317.1647648006.0.membrain-it.technology.   
59         10317.1647648006.0.membrain-it.technology.   
60         10317.1647648006.0.membrain-it.technology.   
61         10317.1647648006.0.membrain-it.technology.   
62         10317.1647648006.0.membrain-it.technology.   
...                                               ...   
12129383  55662.1648224046.21.membrain-it.technology.   
12129395  55833.1648224039.21.membrain-it.technology.   
12129396  55833.1648224039.21.membrain-it.technology.   
12129397  55833.1648224039.21.membrain-it.technology.   
12129398  55833.1648224039.21.membrain-it.technology.   

                                                       abuf  \
58        ammDgAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
59        ammDgAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
60        ammDgAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
61        ammDgAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
62        ammDgAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12129383  hH+BgAABAEgAAAABBTU1NjYyCjE2NDgyMjQwNDYCMjELbW...   
12129395  dE6DgAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   
12129396  dE6DgAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   
12129397  dE6DgAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   
12129398  dE6DgAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   

                                                       qbuf  \
58        amkBAAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
59        amkBAAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
60        amkBAAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
61        amkBAAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
62        amkBAAABAAAAAAABBTEwMzE3CjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12129383  hH8BAAABAAAAAAABBTU1NjYyCjE2NDgyMjQwNDYCMjELbW...   
12129395  dE4BAAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   
12129396  dE4BAAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   
12129397  dE4BAAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   
12129398  dE4BAAABAAAAAAABBTU1ODMzCjE2NDgyMjQwMzkCMjELbW...   

         use_probe_resolver  ...  raw_data  flags  \
58                     None  ...      None          
59                     None  ...      None          
60                     None  ...      None          
61                     None  ...      None          
62                     None  ...      None          
...                     ...  ...       ...    ...   
12129383               True  ...      None     cd   
12129395               True  ...      None     cd   
12129396               True  ...      None     cd   
12129397               True  ...      None     cd   
12129398               True  ...      None     cd   

                                             header  query_count  ans_count  \
58        opcode: QUERY, status: NOERROR, id: 49148          1.0        0.0   
59        opcode: QUERY, status: NOERROR, id: 49148          1.0        0.0   
60

In [29]:
request_data = [("2KB", data_2kb),("4KB", data_4kb), ("Both", data_both_response_sizes)]

In [ ]:
names_sequence_data = []
disctinct_sequences = []
for key, df in request_data:
    grouping = df.groupby("question_name")
    sequence_dict = {}
    name_to_sequence = {}
    for name, group in grouping:

        protos = group["proto"].values
        sequence = ",".join(protos)
        name_to_sequence[name] = sequence
        if sequence not in disctinct_sequences and key != "Both":
            disctinct_sequences.append(sequence)
        if sequence in sequence_dict:
            value = sequence_dict[sequence]
            sequence_dict[sequence] = value + 1
        else:
            sequence_dict[sequence] = 1
    counts_df = pd.DataFrame(sequence_dict.items(), columns=["sequence", "count"]).sort_values("count", ascending = False).head(10)
    names_sequence_data.append((key, pd.DataFrame(name_to_sequence.items(), columns=["name", "sequence"])))
    display(counts_df)

In [ ]:
len(disctinct_sequences)

In [ ]:
merged = []
for key, df in request_data: 
    data = None
    if key == "2KB":
        data = names_sequence_data[0][1] 
    elif key=="4KB":
        data = names_sequence_data[1][1] 
    else: 
        data = names_sequence_data[2][1]
    df = df.merge(data, left_on="question_name", right_on="name")
    merged.append((key, df))
request_data = merged 

In [ ]:
fallback_data = []
for key, df in request_data:
    fallback_data.append((f"{key} IPv4", df[df["af"] == 4]))
    fallback_data.append((f"{key} IPv6", df[df["af"] == 6]))  

In [ ]:
for key, df in fallback_data:
    print(key)
    df = df[df["resolver"] != "Comodo"]
    df = df[df["resolver"] != "Probe Resolver"]
    df = df.groupby(["question_name"]).head(1)
    #display(pd.crosstab(df["status"], df["resolver"], margins=True))
    ct = pd.crosstab(df["resolver"], df["status"], normalize="index", margins=True)
    display(ct)
    print(ct.to_latex(float_format='{:,.2%}'.format))

# Protocols used for first/second request

In [469]:
for key, df in fallback_data:
    counts = df.groupby("question_name", as_index=False).size()
    question_names_relevant = counts[counts["size"] <= 2]["question_name"].unique()
    head = df[df["question_name"].isin(question_names_relevant)].groupby("question_name").head(1)
    tail = df[df["question_name"].isin(question_names_relevant)].groupby("question_name").tail(1)
    print(key)
    print("First requests")
    display(head["proto"].value_counts(normalize=True))
    print("Last requests")
    display(tail["proto"].value_counts(normalize=True))

2KB IPv4
First requests


UDP    0.998427
TCP    0.001573
Name: proto, dtype: float64

Last requests


TCP    0.775252
UDP    0.224748
Name: proto, dtype: float64

2KB IPv6
First requests


...

UDP    0.936334
TCP    0.063666
Name: proto, dtype: float64

Both IPv6
First requests


UDP    0.91055
TCP    0.08945
Name: proto, dtype: float64

Last requests


UDP    0.931193
TCP    0.068807
Name: proto, dtype: float64

# Requests from different IP addresses

In [470]:
for key, df in fallback_data:
    df = df.groupby(by=["question_name", "backend_resolver"], as_index=False).size().sort_values("size", ascending=False)
    df = df.groupby("question_name", as_index=False).size()
    display(df[df["size"] <= 2])
    display(df[df["size"] > 2])
   

question_name  size
0         10001.1647648006.1.membrain-it.technology.     2
1         10001.1647648012.2.membrain-it.technology.     1
2         10001.1647648019.5.membrain-it.technology.     1
3         10001.1647648025.6.membrain-it.technology.     1
4         10001.1647648037.9.membrain-it.technology.     1
...                                              ...   ...
1557722   55859.1648234817.5.membrain-it.technology.     1
1557723  55859.1648234823.10.membrain-it.technology.     2
1557724   55859.1648234824.3.membrain-it.technology.     1
1557725   55859.1648234825.9.membrain-it.technology.     1
1557726   55859.1648234835.6.membrain-it.technology.     1

[1548759 rows x 2 columns]

question_name  size
3235     10046.1647658876.10.membrain-it.technology.     4
3323     10046.1647712847.10.membrain-it.technology.     4
3334     10046.1647734452.10.membrain-it.technology.     4
3350     10046.1647745268.10.membrain-it.technology.     4
3370     10046.1647756025.10.membrain-it.technology.     4
...                                              ...   ...
1556720  55833.1648026048.10.membrain-it.technology.     3
1556787  55833.1648090828.10.membrain-it.technology.     3
1556865  55833.1648166448.10.membrain-it.technology.     3
1556914  55833.1648206043.10.membrain-it.technology.     3
1556955  55833.1648234877.10.membrain-it.technology.     3

[8968 rows x 2 columns]

question_name  size
0       10001.1647648024.11.membrain-it.technology.     1
1       10001.1647648028.18.membrain-it.technology.     1
2       10001.1647648029.14.membrain-it.technology.     1
3       10001.1647648033.20.membrain-it.technology.     1
4       10001.1647648050.13.membrain-it.technology.     1
...                                             ...   ...
709342  55833.1648234891.12.membrain-it.technology.     2
709343  55833.1648234894.13.membrain-it.technology.     1
709344  55833.1648234897.14.membrain-it.technology.     1
709345  55833.1648234899.18.membrain-it.technology.     1
709346  55833.1648234902.20.membrain-it.technology.     1

[707390 rows x 2 columns]

question_name  size
2583    10099.1647655289.21.membrain-it.technology.     4
2611    10099.1647673264.21.membrain-it.technology.     4
2685    10099.1647738042.21.membrain-it.technology.     4
2700    10099.1647748853.21.membrain-it.technology.     4
2708    10099.1647756040.21.membrain-it.technology.     4
...                                             ...   ...
709201  55833.1648123265.21.membrain-it.technology.     3
709215  55833.1648134055.21.membrain-it.technology.     3
709249  55833.1648170047.21.membrain-it.technology.     3
709257  55833.1648177249.21.membrain-it.technology.     3
709347  55833.1648234910.21.membrain-it.technology.     3

[1958 rows x 2 columns]

question_name  size
0       10001.1647648006.0.membrain-it.technology.     1
1       10001.1647648011.3.membrain-it.technology.     1
2       10001.1647655217.5.membrain-it.technology.     1
3       10001.1647658812.2.membrain-it.technology.     1
4       10001.1647658818.5.membrain-it.technology.     1
...                                            ...   ...
620224  55859.1648224012.3.membrain-it.technology.     1
620225  55859.1648224013.1.membrain-it.technology.     2
620226  55859.1648224019.5.membrain-it.technology.     1
620227  55859.1648224028.8.membrain-it.technology.     1
620228  55859.1648224040.9.membrain-it.technology.     1

[616146 rows x 2 columns]

...

question_name  size
987     10099.1647781231.21.membrain-it.technology.     3
15420   11570.1647943235.21.membrain-it.technology.     3
17558   11760.1647698451.21.membrain-it.technology.     4
17606   11760.1647792039.21.membrain-it.technology.     4
17643   11760.1647856871.21.membrain-it.technology.     4
...                                             ...   ...
293567  55662.1648083635.21.membrain-it.technology.     3
293587  55662.1648112436.21.membrain-it.technology.     3
293619  55662.1648173641.21.membrain-it.technology.     3
295519  55776.1647774024.12.membrain-it.technology.     3
296250  55817.1648090891.21.membrain-it.technology.     3

[1123 rows x 2 columns]

question_name  size
0        10001.1647648019.8.membrain-it.technology.     1
1        10001.1647655244.9.membrain-it.technology.     1
2        10001.1647658823.9.membrain-it.technology.     1
3        10001.1647662435.9.membrain-it.technology.     1
4        10001.1647669637.8.membrain-it.technology.     1
...                                             ...   ...
414342   55859.1648206040.9.membrain-it.technology.     1
414343   55859.1648209624.9.membrain-it.technology.     1
414344  55859.1648209639.10.membrain-it.technology.     2
414345   55859.1648216814.6.membrain-it.technology.     1
414346   55859.1648216829.8.membrain-it.technology.     2

[375016 rows x 2 columns]

question_name  size
627      10046.1647651610.1.membrain-it.technology.     3
628     10046.1647651623.10.membrain-it.technology.     4
657     10046.1647795663.10.membrain-it.technology.     4
663     10046.1647820866.10.membrain-it.technology.     4
664     10046.1647828042.10.membrain-it.technology.     4
...                                             ...   ...
414133  55833.1648173655.10.membrain-it.technology.     3
414138  55833.1648191651.10.membrain-it.technology.     3
414140  55833.1648195236.10.membrain-it.technology.     3
414147  55833.1648220428.10.membrain-it.technology.     3
414150  55833.1648224035.10.membrain-it.technology.     3

[39331 rows x 2 columns]

question_name  size
0       10001.1647658955.19.membrain-it.technology.     1
1       10001.1647662509.20.membrain-it.technology.     1
2       10001.1647669676.19.membrain-it.technology.     2
3       10001.1647673300.19.membrain-it.technology.     2
4       10001.1647676876.19.membrain-it.technology.     1
...                                             ...   ...
111540  55833.1648216871.19.membrain-it.technology.     1
111541  55833.1648216873.20.membrain-it.technology.     1
111542  55833.1648220433.19.membrain-it.technology.     2
111543  55833.1648224039.21.membrain-it.technology.     2
111544  55833.1648224044.19.membrain-it.technology.     2

[102170 rows x 2 columns]

question_name  size
258     10099.1647658871.21.membrain-it.technology.     4
261     10099.1647669638.21.membrain-it.technology.     4
263     10099.1647676859.21.membrain-it.technology.     4
271     10099.1647694838.21.membrain-it.technology.     4
272     10099.1647698469.21.membrain-it.technology.     4
...                                             ...   ...
111529  55833.1648180880.21.membrain-it.technology.     3
111531  55833.1648184445.21.membrain-it.technology.     3
111535  55833.1648195247.21.membrain-it.technology.     3
111536  55833.1648202471.21.membrain-it.technology.     3
111539  55833.1648209644.21.membrain-it.technology.     3

[9375 rows x 2 columns]

### UDP->TCP come from different IPs

In [471]:
for key, df in fallback_data: 
    print(key)
    df = df[df["sequence"] == "UDP,TCP"]
    counts = df.groupby(["backend_resolver", "question_name"], as_index = False).size()
    counts = counts.groupby("question_name", as_index = False).size().sort_values("size", ascending=False)
    display(counts.value_counts("size", normalize=True))

2KB IPv4


size
1    0.789869
2    0.210131
dtype: float64

2KB IPv6


size
1    0.823837
2    0.176163
dtype: float64

4KB IPv4


...

size
1    0.76529
2    0.23471
dtype: float64

Both IPv4


size
1    0.913043
2    0.086957
dtype: float64

Both IPv6


size
1    1.0
dtype: float64

# Canonical vs. non-canonical

In [135]:
def create_type_column(row):
    if row["sequence"] == "UDP,TCP":
        return "canoncial"
    if row["sequence"] == "UDP":
        return "no fallback UDP"
    if row["sequence"] == "TCP":
        return "no fallback TCP"
    else:
        return "non-canonical"
    
def create_tcp_column(row):
    if "TCP" in row["sequence"]:
        return True
    return False

def create_tcp_end_column(row):
    if row["sequence"].endswith("TCP"):
        return True
    return False


In [136]:
for i in range(len(fallback_data)):
    key, df = fallback_data[i]
    df["type"] = df.apply(create_type_column , axis = 1)
    df["is_tcp_used"] = df.apply(create_tcp_column , axis = 1)
    df["endwith_tcp"] = df.apply(create_tcp_end_column , axis = 1)
    fallback_data[i] = (key,df)


/tmp/ipykernel_24349/3292027187.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["type"] = df.apply(create_type_column , axis = 1)
/tmp/ipykernel_24349/3292027187.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["is_tcp_used"] = df.apply(create_tcp_column , axis = 1)
/tmp/ipykernel_24349/3292027187.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https:/

In [35]:
for key, df in fallback_data: 
    print(key)
    df = df.groupby(["question_name"]).tail(1)
    display(df.value_counts("type", normalize = True))

2KB IPv4


type
canoncial          0.603793
non-canonical      0.385067
no fallback UDP    0.009950
no fallback TCP    0.001189
dtype: float64

2KB IPv6


type
canoncial          0.688665
non-canonical      0.298429
no fallback UDP    0.011615
no fallback TCP    0.001291
dtype: float64

4KB IPv4


...

type
canoncial          0.751882
non-canonical      0.237635
no fallback UDP    0.008700
no fallback TCP    0.001783
dtype: float64

Both IPv4


type
non-canonical    0.999944
canoncial        0.000056
dtype: float64

Both IPv6


type
non-canonical    0.999991
canoncial        0.000009
dtype: float64

In [138]:
for key, df in fallback_data: 
    print(key)
    df = df[df["resolver"] != "Probe Resolver"]
    df = df.groupby(["question_name", "sequence"]).tail(1)
    ct = pd.crosstab(df["resolver"], df["type"])
    display(ct)
    ct = pd.crosstab(df["resolver"], df["type"], normalize = "index", margins=True)
    print(ct.columns.tolist())
    ct = ct.rename(columns={"canoncial": "Canonical", "no fallback TCP": "Single TCP", "no fallback UDP": "Single UDP", "non-canonical": "Non-Canonical"})
    ct = ct[["Canonical", "Non-Canonical", "Single UDP"]]
    display(ct)
    print(ct.to_latex(float_format='{:,.2%}'.format))

2KB IPv4


type           canoncial  no fallback UDP  non-canonical
resolver                                                
CleanBrowsing     229154              264           1081
Cloudflare        151043              303           7041
Comodo              1936             1588         158531
Google            176026              169           1182
Neustar             1861             1542         138916
OpenDNS           182216              391           3885
OpenNIC             1775              278           1135
Quad9              76125              314          88550
UncensoredDNS      26391              333           1318
Yandex              2001             1707         164425

['canoncial', 'no fallback UDP', 'non-canonical']


type           Canonical  Non-Canonical  Single UDP
resolver                                           
CleanBrowsing   0.994165       0.004690    0.001145
Cloudflare      0.953633       0.044454    0.001913
Comodo          0.011947       0.978254    0.009799
Google          0.992383       0.006664    0.000953
Neustar         0.013076       0.976089    0.010835
OpenDNS         0.977071       0.020832    0.002097
OpenNIC         0.556775       0.356023    0.087202
Quad9           0.461394       0.536702    0.001903
UncensoredDNS   0.941124       0.047001    0.011875
Yandex          0.011901       0.977946    0.010153
All             0.596932       0.398221    0.004846

\begin{tabular}{lrrr}
\toprule
type &  Canonical &  Non-Canonical &  Single UDP \\
resolver      &            &                &             \\
\midrule
CleanBrowsing &     99.42\% &          0.47\% &       0.11\% \\
Cloudflare    &     95.36\% &          4.45\% &       0.19\% \\
Comodo        &      1.19\% &         97.83\% &       0.98\% \\
Google        &     99.24\% &          0.67\% &       0.10\% \\
Neustar       &      1.31\% &         97.61\% &       1.08\% \\
OpenDNS       &     97.71\% &          2.08\% &       0.21\% \\
OpenNIC       &     55.68\% &         35.60\% &       8.72\% \\
Quad9         &     46.14\% &         53.67\% &       0.19\% \\
UncensoredDNS &     94.11\% &          4.70\% &       1.19\% \\
Yandex        &      1.19\% &         97.79\% &       1.02\% \\
All           &     59.69\% &         39.82\% &       0.48\% \\
\bottomrule
\end{tabular}

2KB IPv6


...

type           Canonical  Non-Canonical  Single UDP
resolver                                           
CleanBrowsing   0.988308       0.002454    0.009237
Cloudflare      0.852384       0.143735    0.003554
Google          0.988170       0.001884    0.009946
Neustar         0.007314       0.982491    0.010195
OpenDNS         0.983827       0.007882    0.008291
OpenNIC         0.383436       0.070552    0.546012
Quad9           0.312307       0.682098    0.005595
UncensoredDNS   0.994845       0.001093    0.004061
Yandex          0.008281       0.978600    0.013118
All             0.754267       0.237917    0.007754

\begin{tabular}{lrrr}
\toprule
type &  Canonical &  Non-Canonical &  Single UDP \\
resolver      &            &                &             \\
\midrule
CleanBrowsing &     98.83\% &          0.25\% &       0.92\% \\
Cloudflare    &     85.24\% &         14.37\% &       0.36\% \\
Google        &     98.82\% &          0.19\% &       0.99\% \\
Neustar       &      0.73\% &         98.25\% &       1.02\% \\
OpenDNS       &     98.38\% &          0.79\% &       0.83\% \\
OpenNIC       &     38.34\% &          7.06\% &      54.60\% \\
Quad9         &     31.23\% &         68.21\% &       0.56\% \\
UncensoredDNS &     99.48\% &          0.11\% &       0.41\% \\
Yandex        &      0.83\% &         97.86\% &       1.31\% \\
All           &     75.43\% &         23.79\% &       0.78\% \\
\bottomrule
\end{tabular}

Both IPv4


type           non-canonical
resolver                    
CleanBrowsing           3395
Cloudflare             11594
Comodo                 97479
Google                  2720
Neustar               103893
OpenDNS                16982
OpenNIC                 2459
Quad9                  28578
UncensoredDNS           2267
Yandex                 79499

['non-canonical']


KeyError: "['Canonical', 'Single UDP'] not in index"

In [184]:
for key, df in fallback_data: 
    print(key)
    df = df[df["resolver"] != "Probe Resolver"]
    df = df.groupby(["question_name", "sequence"]).tail(1)
    ct = pd.crosstab(df["status"], df["type"], normalize = "columns", margins=True)
    ct = ct.rename(columns={"canoncial": "Canonical", "no fallback TCP": "Single TCP", "no fallback UDP": "Single UDP", "non-canonical": "Non-Canonical"})
    ct = ct[["Canonical", "Non-Canonical", "Single UDP", "All"]]
    display(ct)
    print(ct.to_latex(float_format='{:,.2%}'.format))

2KB IPv4


type     Canonical  Non-Canonical  Single UDP       All
status                                                 
failure   0.031318       0.084353     0.19161  0.053214
ok        0.968682       0.915647     0.80839  0.946786

\begin{tabular}{lrrrr}
\toprule
type &  Canonical &  Non-Canonical &  Single UDP &    All \\
status  &            &                &             &        \\
\midrule
failure &      3.13\% &          8.44\% &      19.16\% &  5.32\% \\
ok      &     96.87\% &         91.56\% &      80.84\% & 94.68\% \\
\bottomrule
\end{tabular}

2KB IPv6


type     Canonical  Non-Canonical  Single UDP       All
status                                                 
failure   0.202456       0.304032    0.298497  0.233867
ok        0.797544       0.695968    0.701503  0.766133

\begin{tabular}{lrrrr}
\toprule
type &  Canonical &  Non-Canonical &  Single UDP &    All \\
status  &            &                &             &        \\
\midrule
failure &     20.25\% &         30.40\% &      29.85\% & 23.39\% \\
ok      &     79.75\% &         69.60\% &      70.15\% & 76.61\% \\
\bottomrule
\end{tabular}

4KB IPv4


type     Canonical  Non-Canonical  Single UDP       All
status                                                 
failure    0.01247       0.059844    0.168741  0.026394
ok         0.98753       0.940156    0.831259  0.973606

\begin{tabular}{lrrrr}
\toprule
type &  Canonical &  Non-Canonical &  Single UDP &    All \\
status  &            &                &             &        \\
\midrule
failure &      1.25\% &          5.98\% &      16.87\% &  2.64\% \\
ok      &     98.75\% &         94.02\% &      83.13\% & 97.36\% \\
\bottomrule
\end{tabular}

4KB IPv6


type     Canonical  Non-Canonical  Single UDP       All
status                                                 
failure   0.023182       0.029454    0.050907  0.024888
ok        0.976818       0.970546    0.949093  0.975112

\begin{tabular}{lrrrr}
\toprule
type &  Canonical &  Non-Canonical &  Single UDP &    All \\
status  &            &                &             &        \\
\midrule
failure &      2.32\% &          2.95\% &       5.09\% &  2.49\% \\
ok      &     97.68\% &         97.05\% &      94.91\% & 97.51\% \\
\bottomrule
\end{tabular}

Both IPv4


KeyError: "['Canonical', 'Single UDP'] not in index"

In [477]:
for key, df in fallback_data: 
    for resolver, df_resolver in df.groupby("resolver"):
        df_resolver = df_resolver.groupby(["question_name", "sequence"]).tail(1)
        print(resolver)
        display(pd.crosstab(df_resolver["status"], df_resolver["type"], normalize = "columns"))
        

CleanBrowsing


type     canoncial  no fallback UDP  non-canonical
status                                            
failure   0.007471         0.359848       0.094357
ok        0.992529         0.640152       0.905643

Cloudflare


type     canoncial  no fallback UDP  non-canonical
status                                            
failure   0.004012         0.207921       0.016049
ok        0.995988         0.792079       0.983951

Comodo


...

type     non-canonical
status                
failure       0.292915
ok            0.707085

UncensoredDNS


type     non-canonical
status                
failure       0.048889
ok            0.951111

Yandex


type     non-canonical
status                
failure       0.038632
ok            0.961368

## TCP usage in general

In [38]:
for key, df in fallback_data: 
    print(key)
    df = df.groupby(["question_name", "sequence"]).tail(1)
    display(df.value_counts("is_tcp_used", normalize=True))
    display(df.value_counts("endwith_tcp", normalize=True))

2KB IPv4


is_tcp_used
True     0.766961
False    0.233039
dtype: float64

endwith_tcp
True     0.734739
False    0.265261
dtype: float64

2KB IPv6


is_tcp_used
True     0.846152
False    0.153848
dtype: float64

...

is_tcp_used
True     0.974063
False    0.025937
dtype: float64

endwith_tcp
True     0.898609
False    0.101391
dtype: float64

Both IPv6


is_tcp_used
True     0.99021
False    0.00979
dtype: float64

endwith_tcp
True     0.933049
False    0.066951
dtype: float64

## TCP usage non-canonical cases

In [39]:
for key, df in fallback_data: 
    print(key)
    df = df[df["type"] == "non-canonical"]
    df = df.groupby(["question_name", "sequence"]).tail(1)
    display(df.value_counts("is_tcp_used", normalize=True))
    display(df.value_counts("endwith_tcp", normalize=True))

2KB IPv4


is_tcp_used
False    0.579349
True     0.420651
dtype: float64

endwith_tcp
False    0.66303
True     0.33697
dtype: float64

2KB IPv6


is_tcp_used
True     0.523393
False    0.476607
dtype: float64

...

is_tcp_used
True     0.974061
False    0.025939
dtype: float64

endwith_tcp
True     0.898604
False    0.101396
dtype: float64

Both IPv6


is_tcp_used
True     0.99021
False    0.00979
dtype: float64

endwith_tcp
True     0.933049
False    0.066951
dtype: float64

In [144]:
for key, df in fallback_data: 
    print(key)
    df = df[df["resolver"] != "Probe Resolver"]
    df = df.groupby(["question_name", "sequence"]).tail(1)
    ct_used = pd.crosstab(df["status"], df["is_tcp_used"], normalize = "columns")
    ct_end = pd.crosstab(df["status"], df["endwith_tcp"], normalize = "columns")
    
    
    ct_used = ct_used.rename(columns={True: "TCP Used", False: "No TCP Used"})
    ct_used = ct_used[["TCP Used", "No TCP Used"]]

    ct_end = ct_end.rename(columns={True: "Last Request TCP", False: "Last Request UDP"})
    ct_end = ct_end[["Last Request TCP", "Last Request UDP"]]
    
    display(ct_used)
    print(ct_used.to_latex(float_format='{:,.2%}'.format))
    display(ct_end)
    print(ct_end.to_latex(float_format='{:,.2%}'.format))

2KB IPv4


is_tcp_used  TCP Used  No TCP Used
status                            
failure       0.04583     0.075799
ok            0.95417     0.924201

\begin{tabular}{lrr}
\toprule
is\_tcp\_used &  TCP Used &  No TCP Used \\
status  &           &              \\
\midrule
failure &     4.58\% &        7.58\% \\
ok      &    95.42\% &       92.42\% \\
\bottomrule
\end{tabular}



endwith_tcp  Last Request TCP  Last Request UDP
status                                         
failure              0.041389          0.083579
ok                   0.958611          0.916421

\begin{tabular}{lrr}
\toprule
endwith\_tcp &  Last Request TCP &  Last Request UDP \\
status  &                   &                   \\
\midrule
failure &             4.14\% &             8.36\% \\
ok      &            95.86\% &            91.64\% \\
\bottomrule
\end{tabular}

2KB IPv6


...

\begin{tabular}{lrr}
\toprule
endwith\_tcp &  Last Request TCP &  Last Request UDP \\
status  &                   &                   \\
\midrule
failure &            17.97\% &            19.65\% \\
ok      &            82.03\% &            80.35\% \\
\bottomrule
\end{tabular}

Both IPv6


is_tcp_used  TCP Used  No TCP Used
status                            
failure      0.181172     0.200965
ok           0.818828     0.799035

\begin{tabular}{lrr}
\toprule
is\_tcp\_used &  TCP Used &  No TCP Used \\
status  &           &              \\
\midrule
failure &    18.12\% &       20.10\% \\
ok      &    81.88\% &       79.90\% \\
\bottomrule
\end{tabular}



endwith_tcp  Last Request TCP  Last Request UDP
status                                         
failure              0.181132          0.183805
ok                   0.818868          0.816195

\begin{tabular}{lrr}
\toprule
endwith\_tcp &  Last Request TCP &  Last Request UDP \\
status  &                   &                   \\
\midrule
failure &            18.11\% &            18.38\% \\
ok      &            81.89\% &            81.62\% \\
\bottomrule
\end{tabular}



## TCP usage per resolver

In [143]:
for key, df in fallback_data: 
    print(key)
    df = df[df["resolver"] != "Probe Resolver"]
    df = df.groupby(["question_name", "sequence"]).tail(1)
    ct_used = pd.crosstab(df["resolver"], df["is_tcp_used"], normalize="index", margins = True)
    ct_end = pd.crosstab(df["resolver"], df["endwith_tcp"], normalize="index",margins=True)
    ct_used = ct_used.rename(columns={True: "TCP Used", False: "No TCP Used"})
    display(ct_used.columns.tolist())
    ct_used = ct_used[["TCP Used", "No TCP Used"]]

    ct_end = ct_end.rename(columns={True: "Last Request TCP", False: "Last Request UDP"})
    ct_end = ct_end[["Last Request TCP", "Last Request UDP"]]
    
    display(ct_used)
    print(ct_used.to_latex(float_format='{:,.2%}'.format))
    display(ct_end)
    print(ct_end.to_latex(float_format='{:,.2%}'.format))

2KB IPv4


['No TCP Used', 'TCP Used']

is_tcp_used    TCP Used  No TCP Used
resolver                            
CleanBrowsing  0.998364     0.001636
Cloudflare     0.997443     0.002557
Comodo         0.079356     0.920644
Google         0.998624     0.001376
Neustar        0.735229     0.264771
OpenDNS        0.997335     0.002665
OpenNIC        0.880489     0.119511
Quad9          0.997442     0.002558
UncensoredDNS  0.983418     0.016582
Yandex         0.044869     0.955131
All            0.753597     0.246403

\begin{tabular}{lrr}
\toprule
is\_tcp\_used &  TCP Used &  No TCP Used \\
resolver      &           &              \\
\midrule
CleanBrowsing &    99.84\% &        0.16\% \\
Cloudflare    &    99.74\% &        0.26\% \\
Comodo        &     7.94\% &       92.06\% \\
Google        &    99.86\% &        0.14\% \\
Neustar       &    73.52\% &       26.48\% \\
OpenDNS       &    99.73\% &        0.27\% \\
OpenNIC       &    88.05\% &       11.95\% \\
Quad9         &    99.74\% &        0.26\% \\
UncensoredDNS &    98.34\% &        1.66\% \\
Yandex        &     4.49\% &       95.51\% \\
All           &    75.36\% &       24.64\% \\
\bottomrule
\end{tabular}



endwith_tcp    Last Request TCP  Last Request UDP
resolver                                         
CleanBrowsing          0.997970          0.002030
Cloudflare             0.969511          0.030489
Comodo                 0.033581          0.966419
Google                 0.998140          0.001860
Neustar                0.499554          0.500446
OpenDNS                0.996734          0.003266
OpenNIC                0.851631          0.148369
Quad9                  0.996854          0.003146
UncensoredDNS          0.980422          0.019578
Yandex                 0.031713          0.968287
All                    0.719719          0.280281

...

['No TCP Used', 'TCP Used']

is_tcp_used    TCP Used  No TCP Used
resolver                            
CleanBrowsing  0.843096     0.156904
Cloudflare     0.994836     0.005164
Google         0.845304     0.154696
Neustar        0.997832     0.002168
OpenDNS        0.971823     0.028177
OpenNIC        0.583333     0.416667
Quad9          0.996647     0.003353
UncensoredDNS  0.884444     0.115556
Yandex         0.990143     0.009857
All            0.992734     0.007266

\begin{tabular}{lrr}
\toprule
is\_tcp\_used &  TCP Used &  No TCP Used \\
resolver      &           &              \\
\midrule
CleanBrowsing &    84.31\% &       15.69\% \\
Cloudflare    &    99.48\% &        0.52\% \\
Google        &    84.53\% &       15.47\% \\
Neustar       &    99.78\% &        0.22\% \\
OpenDNS       &    97.18\% &        2.82\% \\
OpenNIC       &    58.33\% &       41.67\% \\
Quad9         &    99.66\% &        0.34\% \\
UncensoredDNS &    88.44\% &       11.56\% \\
Yandex        &    99.01\% &        0.99\% \\
All           &    99.27\% &        0.73\% \\
\bottomrule
\end{tabular}



endwith_tcp    Last Request TCP  Last Request UDP
resolver                                         
CleanBrowsing          0.117155          0.882845
Cloudflare             0.454389          0.545611
Google                 0.497238          0.502762
Neustar                0.988038          0.011962
OpenDNS                0.268545          0.731455
OpenNIC                0.550000          0.450000
Quad9                  0.975749          0.024251
UncensoredDNS          0.168889          0.831111
Yandex                 0.987616          0.012384
All                    0.931041          0.068959

\begin{tabular}{lrr}
\toprule
endwith\_tcp &  Last Request TCP &  Last Request UDP \\
resolver      &                   &                   \\
\midrule
CleanBrowsing &            11.72\% &            88.28\% \\
Cloudflare    &            45.44\% &            54.56\% \\
Google        &            49.72\% &            50.28\% \\
Neustar       &            98.80\% &             1.20\% \\
OpenDNS       &            26.85\% &            73.15\% \\
OpenNIC       &            55.00\% &            45.00\% \\
Quad9         &            97.57\% &             2.43\% \\
UncensoredDNS &            16.89\% &            83.11\% \\
Yandex        &            98.76\% &             1.24\% \\
All           &            93.10\% &             6.90\% \\
\bottomrule
\end{tabular}



In [482]:
for key, df in fallback_data: 
    df = df.groupby(["question_name", "sequence"]).tail(1)
    display(pd.crosstab(df["is_tcp_used"], df["continent"], normalize="columns"))
    display(pd.crosstab(df["endwith_tcp"], df["continent"], normalize="columns"))

continent      Africa      Asia    Europe      None  North America   Oceania  \
is_tcp_used                                                                    
False        0.267971  0.269108  0.230925  0.243153       0.223117  0.271079   
True         0.732029  0.730892  0.769075  0.756847       0.776883  0.728921   

continent    South America  
is_tcp_used                 
False              0.26115  
True               0.73885

continent      Africa      Asia   Europe      None  North America   Oceania  \
endwith_tcp                                                                   
False        0.310709  0.326758  0.26021  0.279225       0.252737  0.356593   
True         0.689291  0.673242  0.73979  0.720775       0.747263  0.643407   

continent    South America  
endwith_tcp                 
False             0.302617  
True              0.697383

continent      Africa    Asia    Europe      None  North America   Oceania  \
is_tcp_used                                                                  
False        0.171884  0.1739  0.148888  0.096154       0.171188  0.154988   
True         0.828116  0.8261  0.851112  0.903846       0.828812  0.845012   

continent    South America  
is_tcp_used                 
False             0.181008  
True              0.818992

continent      Africa      Asia   Europe      None  North America   Oceania  \
endwith_tcp                                                                   
False        0.213333  0.213319  0.17376  0.108516       0.196956  0.249123   
True         0.786667  0.786681  0.82624  0.891484       0.803044  0.750877   

continent    South America  
endwith_tcp                 
False             0.213514  
True              0.786486

continent      Africa      Asia    Europe      None  North America   Oceania  \
is_tcp_used                                                                    
False        0.001579  0.005181  0.001863  0.002994       0.007052  0.005064   
True         0.998421  0.994819  0.998137  0.997006       0.992948  0.994936   

continent    South America  
is_tcp_used                 
False             0.009833  
True              0.990167

...

continent      Africa      Asia    Europe      None  North America   Oceania  \
endwith_tcp                                                                    
False        0.053723  0.041998  0.017268  0.003086       0.020557  0.134071   
True         0.946277  0.958002  0.982732  0.996914       0.979443  0.865929   

continent    South America  
endwith_tcp                 
False             0.035898  
True              0.964102

continent      Africa      Asia    Europe      None  North America   Oceania  \
is_tcp_used                                                                    
False        0.010448  0.014746  0.027318  0.006745       0.024462  0.028763   
True         0.989552  0.985254  0.972682  0.993255       0.975538  0.971237   

continent    South America  
is_tcp_used                 
False             0.046547  
True              0.953453

continent      Africa      Asia    Europe     None  North America  Oceania  \
endwith_tcp                                                                  
False        0.189761  0.146775  0.080184  0.10118       0.114227  0.22596   
True         0.810239  0.853225  0.919816  0.89882       0.885773  0.77404   

continent    South America  
endwith_tcp                 
False             0.175092  
True              0.824908

continent      Africa    Asia    Europe  None  North America   Oceania  \
is_tcp_used                                                              
False        0.002674  0.0035  0.008266   0.0       0.008803  0.022504   
True         0.997326  0.9965  0.991734   1.0       0.991197  0.977496   

continent    South America  
is_tcp_used                 
False             0.061656  
True              0.938344

continent      Africa      Asia    Europe      None  North America   Oceania  \
endwith_tcp                                                                    
False        0.187166  0.122375  0.037465  0.007407       0.105194  0.225035   
True         0.812834  0.877625  0.962535  0.992593       0.894806  0.774965   

continent    South America  
endwith_tcp                 
False             0.179861  
True              0.820139

In [483]:
for key, df in fallback_data: 
    df = df.groupby(["question_name", "sequence"], as_index=False).size()
    df["is_tcp_used"] = df.apply(create_tcp_column , axis = 1)
    df["endwith_tcp"] = df.apply(create_tcp_end_column , axis = 1)
    display(df.value_counts("is_tcp_used", normalize=True))
    display(df.value_counts("endwith_tcp", normalize=True))

is_tcp_used
True     0.766961
False    0.233039
dtype: float64

endwith_tcp
True     0.734739
False    0.265261
dtype: float64

is_tcp_used
True     0.846152
False    0.153848
dtype: float64

endwith_tcp
True     0.819138
False    0.180862
dtype: float64

is_tcp_used
True     0.996714
False    0.003286
dtype: float64

...

endwith_tcp
True     0.97756
False    0.02244
dtype: float64

is_tcp_used
True     0.974063
False    0.025937
dtype: float64

endwith_tcp
True     0.898609
False    0.101391
dtype: float64

is_tcp_used
True     0.99021
False    0.00979
dtype: float64

endwith_tcp
True     0.933049
False    0.066951
dtype: float64

In [170]:
for key, df in merged: 
    df = df[df["sequence"] == "UDP,TCP"]
    df = df.groupby("question_name").head(1)
    display(df.value_counts("udp_size"))


udp_size
1232.0    717560
1400.0    342929
1452.0    311134
1410.0    310940
512.0      48119
1472.0     14671
1680.0      4702
1460.0      4262
1432.0      1362
1220.0      1188
1280.0      1083
2048.0       683
1444.0       631
1480.0       226
1250.0       171
4096.0       153
1231.0       136
850.0         97
1230.0        37
1252.0        14
1415.0        12
1218.0         9
1414.0         5
1260.0         3
2098.0         3
1216.0         3
1412.0         3
1450.0         3
1219.0         2
1440.0         2
1226.0         1
2058.0         1
2084.0         1
2095.0         1
1227.0         1
dtype: int64

udp_size
1232.0    268577
1452.0    213821
1400.0    209502
4096.0    207243
1410.0    122257
512.0      47499
1472.0     20187
1680.0      4245
1460.0      3511
1432.0      1274
1280.0      1055
1220.0       709
2048.0       672
1444.0       606
4000.0       521
4010.0       423
1480.0       213
1250.0       104
1231.0        93
850.0         91
1230.0        23
1252.0        15
1414.0         9
1218.0         7
4075.0         5
1412.0         4
1415.0         3
1260.0         3
4072.0         3
4086.0         2
4087.0         2
1423.0         2
1216.0         2
1226.0         2
1205.0         1
1450.0         1
1215.0         1
1227.0         1
1219.0         1
dtype: int64

In [171]:
for key, df in fallback_data: 
    df = df.groupby("question_name").head(1)
    df = df[df["sequence"] == "UDP"]
    print(key)
    display(df.value_counts("status"))
    display(pd.crosstab(df["udp_size"], df["status"]).sort_values("ok", ascending=False))

2KB


status
ok         180811
failure      2081
dtype: int64

status    failure      ok
udp_size                 
4096.0       1697  168042
1452.0          7    5892
8192.0        167    3134
1410.0          2    2464
4000.0        106     370
4010.0         10     364
1232.0         58     208
1400.0          1     158
512.0          11      86
1460.0          0      39
1472.0          2      13
2099.0          0       3
1680.0          0       2
1220.0          0       1
2071.0          0       1
2087.0          0       1
3500.0          4       1
1432.0          1       0
1231.0          1       0
1480.0          2       0

4KB


status
ok         33030
failure      503
dtype: int64

status    failure    ok
udp_size               
1452.0          6  9943
1410.0         26  9195
8192.0         17  4140
4096.0        215  4003
1232.0        124  2014
1400.0          5  1190
1472.0         26   429
512.0          53   386
1460.0          0   121
1680.0          0    52
1231.0          0    20
1432.0          2     9
1220.0          0     8
1480.0          2     2
1230.0          0     1
1219.0          1     0
2048.0          9     0
3500.0          2     0
4000.0          1     0
4010.0          2     0

In [ ]:
for key, df in merged: 
    df = df[df["sequence"] == "UDP,UDP"]
    df_head = df.groupby("question_name").head(1)
    df_tail = df.groupby("question_name").tail(1)
    display(df_head.value_counts("udp_size"))
    display(df_tail.value_counts("udp_size"))

In [488]:
conn = sqlite3.connect("request_data.db")

In [494]:
test_data = pd.read_csv("request_data.csv", delimiter = ";")

In [506]:
def filter_fn(row):
    if test_data["question_name"].count('.') == 5:
        return True
    else:
        return False

In [507]:
test_data = test_data[test_data.apply(filter_fn, axis=1)]

/tmp/ipykernel_30450/3553995981.py:2: FutureWarning: Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. ser.count(level=1) should use ser.groupby(level=1).count().
  if test_data["question_name"].count('.') == 5:


ValueError: Series.count level is only valid with a MultiIndex

In [499]:
def parse_txt_data(data):
        result = {}
        pseudosection_results = []
        for item in data: 
            #print(item)
            if item.startswith("FROM"):
                parts = item.split('_')
                result["backend_resolver"] = parts[1]
            if item.startswith("Protocol"):
                parts = item.split('_')
                result["proto"] = parts[1]
            if item.startswith("opcode"):
                result["header"] = item.replace("&", " ").replace("$", "")
            if item.startswith("flags:"):
                parts = item.split('%')
                result["flags"] = parts[0].replace('flags:', '').replace('&', "")
                for part in parts[1:]:
                    inner_parts = part.split(",")
                    for inner_part in inner_parts:
                        single_items = inner_part.split("&")
                        if single_items[1] == "QUERY:":
                            result["query_count"] = single_items[2]
                        elif single_items[1] == "ANSWER:": 
                            result["ans_count"] = single_items[2]
                        elif single_items[1] == "AUTHORITY:": 
                            result["auth_count"] = single_items[2]
                        elif single_items[1] == "ADDITIONAL:": 
                            result["addit_count"] = single_items[2].replace("$", "")
            if item.startswith("OPT&PSEUDOSECTION"):
                parts = item.split('$%&') #"\n; "
                for part in parts[1:]:
                    inner_parts = part.split(":", 1)
                    res = {
                        "name": inner_parts[0],
                        "content": inner_parts[1].replace("&", " ").replace("$", "").replace(" ", "", 1).replace("%", ";")
                    }
                    if inner_parts[0] == "EDNS":
                        single_items = inner_parts[1].split("&")
                        for i in range(len(single_items)):
                            item_i = single_items[i]
                            if item_i.startswith("udp"):
                                result["udp_size"] = single_items[i+1].replace("$", "")
                    pseudosection_results.append(res)
            if item.startswith("QUESTION&SECTION:"):
                parts = item.split("$%") # "\n;"
                result["question"] = parts[1].replace("?", " ").replace("&", "").replace("$", "") 
        return pseudosection_results

In [523]:
def create_pseudosection_column(row):
    pseudosection_results =  parse_txt_data(row["data"].split(" "))
    return ",".join([item["name"] for item in pseudosection_results])

    

In [35]:
df_merged

msm_id  prb_id  sub_id        rt frontend_proto     dst_addr  \
0         39507178   14604       1  1021.576            UDP      1.1.1.1   
1         39507178   14604       1  1021.576            UDP      1.1.1.1   
2         39507178   29376       1    44.184            UDP      1.1.1.1   
3         39507178   29376       1    44.184            UDP      1.1.1.1   
4         39507178   10001       1   746.388            UDP      1.1.1.1   
...            ...     ...     ...       ...            ...          ...   
12328024  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328025  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328026  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328027  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328028  39712680   55660       2  1606.725            UDP  192.168.4.1   

                                        question_name  \
0          14604.1647647999.0.membrain-it.technology.   
1          14604.1647647999.0.membrain-it.technology.   
2          29376.1647647999.0.membrain-it.technology.   
3          29376.1647647999.0.membrain-it.technology.   
4          10001.1647648006.0.membrain-it.technology.   
...                                               ...   
12328024  55660.1648235147.21.membrain-it.technology.   
12328025  55660.1648235147.21.membrain-it.technology.   
12328026  55660.1648235147.21.membrain-it.technology.   
12328027  55660.1648235147.21.membrain-it.technology.   
12328028  55660.1648235147.21.membrain-it.technology.   

                                                       abuf  \
0         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp2DgAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

                                                       qbuf  \
0         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp0BAAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

         use_probe_resolver  ...  raw_data  flags  \
0                      None  ...      None          
1                      None  ...      None          
2                      None  ...      None          
3                      None  ...      None          
4                      None  ...      None          
...                     ...  ...       ...    ...   
12328024               True  ...      None          
12328025               True  ...      None     cd   
12328026               True  ...      None     cd   
12328027               True  ...      None          
12328028               True  ...      None     cd   

                                             header  query_count  ans_count  \
0         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
1         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
2          opcode: QUERY, 

In [85]:
def get_answer_name(row):
    data_abuf = row["abuf"]
    try:
        test = abuf.AbufParser.parse(base64.b64decode(data_abuf))
        if test is not None and "AnswerSection" in test: 
            return True
        else:
            return False
    except: 
        return False

In [86]:
df_test = df_merged

In [ ]:
df_test["has_answer"] = df_test.apply(get_answer_name, axis=1)

In [88]:
df_test

msm_id  prb_id  sub_id        rt frontend_proto     dst_addr  \
0         39507178   14604       1  1021.576            UDP      1.1.1.1   
1         39507178   14604       1  1021.576            UDP      1.1.1.1   
2         39507178   29376       1    44.184            UDP      1.1.1.1   
3         39507178   29376       1    44.184            UDP      1.1.1.1   
4         39507178   10001       1   746.388            UDP      1.1.1.1   
...            ...     ...     ...       ...            ...          ...   
12328024  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328025  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328026  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328027  39712680   55660       2  1606.725            UDP  192.168.4.1   
12328028  39712680   55660       2  1606.725            UDP  192.168.4.1   

                                        question_name  \
0          14604.1647647999.0.membrain-it.technology.   
1          14604.1647647999.0.membrain-it.technology.   
2          29376.1647647999.0.membrain-it.technology.   
3          29376.1647647999.0.membrain-it.technology.   
4          10001.1647648006.0.membrain-it.technology.   
...                                               ...   
12328024  55660.1648235147.21.membrain-it.technology.   
12328025  55660.1648235147.21.membrain-it.technology.   
12328026  55660.1648235147.21.membrain-it.technology.   
12328027  55660.1648235147.21.membrain-it.technology.   
12328028  55660.1648235147.21.membrain-it.technology.   

                                                       abuf  \
0         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b2DgAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQKDgAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp2DgAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QlqBgAABAEgAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

                                                       qbuf  \
0         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
1         1b0BAAABAAAAAAABBTE0NjA0CjE2NDc2NDc5OTkBMAttZW...   
2         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
3         UQIBAAABAAAAAAABBTI5Mzc2CjE2NDc2NDc5OTkBMAttZW...   
4         yp0BAAABAAAAAAABBTEwMDAxCjE2NDc2NDgwMDYBMAttZW...   
...                                                     ...   
12328024  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328025  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328026  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328027  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   
12328028  QloBAAABAAAAAAABBTU1NjYwCjE2NDgyMzUxNDcCMjELbW...   

         use_probe_resolver  ...  flags  \
0                      None  ...          
1                      None  ...          
2                      None  ...          
3                      None  ...          
4                      None  ...          
...                     ...  ...    ...   
12328024               True  ...          
12328025               True  ...     cd   
12328026               True  ...     cd   
12328027               True  ...          
12328028               True  ...     cd   

                                             header  query_count  ans_count  \
0         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
1         opcode: QUERY, status: NOERROR, id: 52832          1.0        0.0   
2          opcode: QUERY, status: NOERROR, id: 8127          1.0        0.0   
3          opcode: QUERY, status: NOERROR, id: 8127          1.0   

In [91]:
df_backup = df_test

In [92]:
df_test[df_test["status"] == "ok"].value_counts("has_answer")
df_test[df_test["status"] == "ok"].("has_answer", normalize = True)

has_answer
False    5072530
True     4404927
dtype: int64

In [147]:
df_never_requested_ok = df_test[df_test["status_detail"] == "never requested ok"]
abufs_nro = df_never_requested_ok[df_never_requested_ok["has_answer"] == True]["abuf"].unique()

In [152]:
cached_counter = 0 
for a in abufs_nro:
    parsed = abuf.AbufParser.parse(base64.b64decode(a))
    if parsed["AnswerSection"][0]["Address"].startswith("2003:ec:970e:f439:c5fd:30b8:2365"):
        cached_counter += 1

In [153]:
cached_counter

2898

In [154]:
len(abufs_nro)

2898

In [107]:
df_ok = df_test[df_test["status"] == "ok"]

pd.crosstab(df_ok["has_answer"], df_ok["resolver"])
pd.crosstab(df_ok["has_answer"], df_ok["resolver"], normalize="columns")
ct = pd.crosstab(df_ok["resolver"], df_ok["has_answer"], normalize="index")
print(ct.to_latex(float_format='{:,.2%}'.format))

\begin{tabular}{lrr}
\toprule
has\_answer &  False &   True \\
resolver       &        &        \\
\midrule
CleanBrowsing  & 98.45\% &  1.55\% \\
Cloudflare     & 98.37\% &  1.63\% \\
Comodo         & 37.21\% & 62.79\% \\
Google         & 42.83\% & 57.17\% \\
Neustar        & 38.63\% & 61.37\% \\
OpenDNS        &  2.35\% & 97.65\% \\
OpenNIC        & 56.61\% & 43.39\% \\
Probe Resolver & 58.34\% & 41.66\% \\
Quad9          & 56.98\% & 43.02\% \\
UncensoredDNS  & 95.95\% &  4.05\% \\
Yandex         & 35.56\% & 64.44\% \\
\bottomrule
\end{tabular}



In [121]:
df_no_answer = df_ok[df_ok["has_answer"] == False]

In [122]:
abufs = df_no_answer["abuf"].unique()

In [123]:
len(abufs)

1886290

In [131]:
tc_counter = 0
servfail_counter = 0 
for a in abufs:
    parsed = abuf.AbufParser.parse(base64.b64decode(a))
    if parsed is not None and "HEADER" in parsed: 
        if "TC" in parsed["HEADER"]:
            if parsed["HEADER"]["TC"] == True: 
                tc_counter += 1
            elif "ReturnCode" in parsed["HEADER"]:
                if parsed["HEADER"]["ReturnCode"] == "SERVFAIL":
                    servfail_counter += 1 
                else:
                    print(parsed)

{'HEADER': {'ID': 24234, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54739.1647648009.0.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54739.1647648009.0.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 10, 'RDlength': 113, 'MasterServerName': 'fake-for-negative-caching.adguard.com.', 'MaintainerName': 'hostmaster.54739.1647648009.0.membrain-it.technology.', 'Serial': 100500, 'Refresh': 1800, 'Retry': 60, 'Expire': 604800, 'NegativeTtl': 86400}]}
{'HEADER': {'ID': 4268, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54989.1647648013.0.membrain-it.technology.', 'Qtype': 

{'HEADER': {'ID': 58783, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54739.1647648017.5.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54739.1647648017.5.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 10, 'RDlength': 113, 'MasterServerName': 'fake-for-negative-caching.adguard.com.', 'MaintainerName': 'hostmaster.54739.1647648017.5.membrain-it.technology.', 'Serial': 100500, 'Refresh': 1800, 'Retry': 60, 'Expire': 604800, 'NegativeTtl': 86400}]}
{'HEADER': {'ID': 58783, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54989.1647648057.5.membrain-it.technology.', 'Qtype':

{'HEADER': {'ID': 15426, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54739.1647651608.0.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54739.1647651608.0.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 10, 'RDlength': 113, 'MasterServerName': 'fake-for-negative-caching.adguard.com.', 'MaintainerName': 'hostmaster.54739.1647651608.0.membrain-it.technology.', 'Serial': 100500, 'Refresh': 1800, 'Retry': 60, 'Expire': 604800, 'NegativeTtl': 86400}]}
{'HEADER': {'ID': 42030, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54989.1647651607.0.membrain-it.technology.', 'Qtype':

{'HEADER': {'ID': 2643, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54739.1647651626.6.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54739.1647651626.6.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 10, 'RDlength': 113, 'MasterServerName': 'fake-for-negative-caching.adguard.com.', 'MaintainerName': 'hostmaster.54739.1647651626.6.membrain-it.technology.', 'Serial': 100500, 'Refresh': 1800, 'Retry': 60, 'Expire': 604800, 'NegativeTtl': 86400}]}
{'HEADER': {'ID': 57024, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': False, 'RA': False, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 0, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '55190.1647651625.6.membrain-it.technology.', 'Qtype'

{'HEADER': {'ID': 36127, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 0, 'ARCOUNT': 1}, 'QuestionSection': [{'Qname': '11570.1647651634.21.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'EDNS0': {'UDPsize': 4096, 'ExtendedReturnCode': 0, 'Version': 0, 'Z': 0, 'Type': 'OPT', 'Option': [], 'Name': '.'}}
{'HEADER': {'ID': 40962, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 0, 'ARCOUNT': 1}, 'QuestionSection': [{'Qname': '52861.1647651635.21.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'EDNS0': {'UDPsize': 4096, 'ExtendedReturnCode': 0, 'Version': 0, 'Z': 0, 'Type': 'OPT', 'Option': [], 'Name': '.'}}
{'HEADER': {'ID': 29547, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA'

...

{'HEADER': {'ID': 40672, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54989.1648231211.1.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54989.1648231211.1.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 0, 'RDlength': 64, 'MasterServerName': 'a.gtld-servers.net.', 'MaintainerName': 'nstld.verisign-grs.com.', 'Serial': 1800, 'Refresh': 1800, 'Retry': 900, 'Expire': 604800, 'NegativeTtl': 86400}]}
{'HEADER': {'ID': 59428, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': False, 'RA': False, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 0, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '55190.1648231209.1.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}]}
{'HEADER': {'ID': 54148

{'HEADER': {'ID': 36687, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54739.1648231228.6.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54739.1648231228.6.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 10, 'RDlength': 113, 'MasterServerName': 'fake-for-negative-caching.adguard.com.', 'MaintainerName': 'hostmaster.54739.1648231228.6.membrain-it.technology.', 'Serial': 100500, 'Refresh': 1800, 'Retry': 60, 'Expire': 604800, 'NegativeTtl': 86400}]}
{'HEADER': {'ID': 17322, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54989.1648231238.6.membrain-it.technology.', 'Qtype':

{'HEADER': {'ID': 23136, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 0, 'ARCOUNT': 1}, 'QuestionSection': [{'Qname': '11570.1648231294.21.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'EDNS0': {'UDPsize': 4096, 'ExtendedReturnCode': 0, 'Version': 0, 'Z': 0, 'Type': 'OPT', 'Option': [], 'Name': '.'}}
{'HEADER': {'ID': 43588, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54989.1648231276.21.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54989.1648231276.21.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 0, 'RDlength': 64, 'MasterServerName': 'a.gtld-servers.net.', 'MaintainerName': 'nstld.verisign-grs.c

{'HEADER': {'ID': 17584, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54739.1648234817.8.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'AuthoritySection': [{'Name': '54739.1648234817.8.membrain-it.technology.', 'Type': 'SOA', 'Class': 'IN', 'TTL': 10, 'RDlength': 113, 'MasterServerName': 'fake-for-negative-caching.adguard.com.', 'MaintainerName': 'hostmaster.54739.1648234817.8.membrain-it.technology.', 'Serial': 100500, 'Refresh': 1800, 'Retry': 60, 'Expire': 604800, 'NegativeTtl': 86400}]}
{'HEADER': {'ID': 47116, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 1, 'ARCOUNT': 0}, 'QuestionSection': [{'Qname': '54989.1648234823.8.membrain-it.technology.', 'Qtype':

{'HEADER': {'ID': 13805, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 0, 'ARCOUNT': 1}, 'QuestionSection': [{'Qname': '52861.1648234867.21.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'EDNS0': {'UDPsize': 4096, 'ExtendedReturnCode': 0, 'Version': 0, 'Z': 0, 'Type': 'OPT', 'Option': [], 'Name': '.'}}
{'HEADER': {'ID': 55049, 'QR': True, 'OpCode': 'QUERY', 'AA': False, 'TC': False, 'RD': True, 'RA': True, 'Z': 0, 'AD': False, 'CD': False, 'ReturnCode': 'NOERROR', 'QDCOUNT': 1, 'ANCOUNT': 0, 'NSCOUNT': 0, 'ARCOUNT': 1}, 'QuestionSection': [{'Qname': '55328.1648235136.21.membrain-it.technology.', 'Qtype': 'AAAA', 'Qclass': 'IN'}], 'EDNS0': {'UDPsize': 4096, 'ExtendedReturnCode': 0, 'Version': 0, 'Z': 0, 'Type': 'OPT', 'Option': [], 'Name': '.'}}


In [132]:
tc_counter

1836360

In [133]:
servfail_counter

41844

In [98]:
conn_txt = sqlite3.connect("ripe_results_txt.db")
df_test_txt = pd.read_sql("SELECT * FROM results", conn_txt)

In [ ]:
df_test_txt["has_answer"] = df_test_txt.apply(get_answer_name, axis=1)

In [103]:
df_txt_ok = df_test_txt[df_test_txt["rt"] != "None"]

In [106]:
df_txt_ok.value_counts("has_answer", normalize = True)

has_answer
True     0.997893
False    0.002107
dtype: float64